# PAT dual camera input

Corresponding to Fig. 5 in the paper. Tested on a cluster with 32GB memory and a Tesla V100S GPU.

In [1]:
import os

import numpy as np
import cv2 as cv
import matplotlib.pyplot as plt
%matplotlib inline
from tqdm.notebook import tqdm

import torch
import torch.nn as nn
import torch.backends.cudnn as cudnn

from skimage.io import imread, imsave
from skimage.util import img_as_float32, img_as_ubyte

from models import PAT
from ext_utils import find_good_matching_points, _project_mesh_grid_to_indices_cube

In [2]:
# load data
data_folder = '../data/dual_camera_sample'
hr = cv.imread(os.path.join(data_folder, 'hr.png'), cv.IMREAD_UNCHANGED)
hr = cv.cvtColor(hr, cv.COLOR_BGR2GRAY)
lr = cv.imread(os.path.join(data_folder, 'lr.png'), cv.IMREAD_UNCHANGED)
lr = cv.cvtColor(lr, cv.COLOR_BGR2RGB)

In [3]:
# preprocess

# pre-crop for to specific area of interest
hr = hr[268:-768, 1012:-1012]

# resulution gap between hr and lr
gap = (25/1.85)/(5/1.25) #calculated by focal length and pixel pitch
h, w = hr.shape
hs, ws = np.round(h/gap).astype(int), np.round(w/gap).astype(int)

# crop the roughly corresponded low-res image, scale to same magnification
pts1, pts2 = find_good_matching_points(cv.cvtColor(lr, cv.COLOR_RGB2GRAY), 
                                       hr)
M_h2l, _ = cv.findHomography(pts2.reshape(-1,1,2),
                             pts1.reshape(-1,1,2),
                             cv.RANSAC, 5.0)
# get correspondences to find center point
x_h2l, y_h2l = _project_mesh_grid_to_indices_cube((w, h), (4*w, 4*h), M_h2l, 1, 1)
xc, yc = int(x_h2l.mean()), int(y_h2l.mean())
# crop out center part
lr_demo = lr[yc-hs//2:yc-hs//2+hs, xc-ws//2:xc-ws//2+ws]
# scale to the same shape as hr
lr_demo = cv.resize(lr_demo, (w,h), cv.INTER_CUBIC)

del x_h2l, y_h2l

In [4]:
# show input images
fig, axes = plt.subplots(1, 2, figsize=(16,8))
axes[0].imshow(lr_demo)
axes[1].imshow(hr)
plt.show()

In [5]:
# find rough correspondence with SIFT
pts1, pts2 = find_good_matching_points(cv.cvtColor(lr_demo, cv.COLOR_RGB2GRAY), 
                                       hr)
M_h2l, _ = cv.findHomography(pts2.reshape(-1,1,2),
                             pts1.reshape(-1,1,2),
                             cv.RANSAC, 5.0)
yys, xxs = _project_mesh_grid_to_indices_cube((w, h), (w, h), M_h2l, 8, 1) # original PAT abuse x/y 
                                                                           # for first/second index

In [15]:
# Demonstrate receptive window
lr_demo2 = lr_demo.astype(float)/255.0
hr_demo = np.stack([hr.astype(float)/255.0 for _ in range(3)], -1)
sample_xy_list = [(990, 815), (1060, 995), (1255, 1150)]
color_list = [(1,0,0), (0,1,0), (0,0,1)]
disp_roi = ((700, 1400), (1400, 700))

fig, axes = plt.subplots(1, 2, figsize=(22,12))
axes[0].imshow(hr_demo)

for (x, y), c in zip(sample_xy_list, color_list):
    axes[0].scatter(x, y, s=200, color=c, marker='x', linewidths=4)
    for hrx, hry in zip(xxs[y,x], yys[y,x]):
        lr_demo2[hrx, hry] = np.array(c)

axes[1].imshow(lr_demo2)

axes[0].set_xlim(*disp_roi[0])
axes[1].set_xlim(*disp_roi[0])
axes[0].set_ylim(*disp_roi[1])
axes[1].set_ylim(*disp_roi[1])

axes[0].set_axis_off()
axes[1].set_axis_off()

plt.show()

In [6]:
# load network
net = PAT(1, in_channel=3, num_input=2).to('cuda')
net = nn.DataParallel(net)
net.eval()
cudnn.benchmark = True
pretrained_dict = torch.load('./weights/dual_input_weights.pth.tar')
net.load_state_dict(pretrained_dict['state_dict'])

<All keys matched successfully>

In [7]:
# get query, key, and value matrices

img0 = img_as_float32(hr)[..., np.newaxis].repeat(3, axis=2)
img1 = img_as_float32(lr_demo)

img_left  = torch.from_numpy(img0.transpose((2, 0, 1))).unsqueeze(0).to('cuda')
img_right = torch.from_numpy(img1.transpose((2, 0, 1))).unsqueeze(0).to('cuda')

with torch.no_grad():
    x_left = net.module.init_feature(img_left)
    x_right = net.module.init_feature(img_right)
    buffer_left = net.module.pam.rb(x_left)
    buffer_right = net.module.pam.rb(x_right)
    Q = net.module.pam.b1(buffer_left)
    K = net.module.pam.b2s[0](buffer_right)
    V = net.module.pam.b3s[0](buffer_right)

In [8]:
# apply attention block by block

pw = 200 # patch width
m, n = np.ceil(h/pw).astype(int), np.ceil(w/pw).astype(int)
i_list, j_list = np.meshgrid(np.arange(m), np.arange(n), indexing='ij')
with torch.no_grad():
    fused_feature = torch.zeros((1, 128, h, w)).float().to('cuda')
    for (i, j) in tqdm(np.stack([i_list, j_list], axis=-1).reshape(-1, 2)):
        xl, xu, yl, yu = i*pw, i*pw+pw, j*pw, j*pw+pw

        Q_ = Q[:, :, xl:xu,yl:yu].contiguous()
        Po = (torch.from_numpy(xxs[xl:xu,yl:yu][np.newaxis]), 
              torch.from_numpy(yys[xl:xu,yl:yu][np.newaxis]))

        buffer, _ = net.module.pam.fe_pam(Q_, K, V, Po, False)
        buffers = [buffer, x_left[:,:,xl:xu,yl:yu]]
        fused_feature[:,:,xl:xu,yl:yu] = torch.cat(tuple(buffers), 1)
        
    # decode final result
    out = net.module.pam.fusion(fused_feature)
    out = net.module.upscale(out)
    
pred = torch.clamp(out, 0, 1).squeeze().cpu().numpy().transpose(1, 2, 0)
del yys, xxs

  0%|          | 0/100 [00:00<?, ?it/s]

In [9]:
# show predicted image
plt.figure(figsize=(16,16))
plt.imshow(pred)
plt.show()

In [ ]:
# save input and predicted images
subfolder = os.path.join("../results", "pat_dual_camera")
if not os.path.exists(subfolder):
    os.mkdir(subfolder)
imsave(os.path.join(subfolder, 'lr.png'), lr_demo)
imsave(os.path.join(subfolder, 'hr.png'), hr)
imsave(os.path.join(subfolder, 'pred.png'), img_as_ubyte(pred))